# OISST: SST Data

https://www.ncei.noaa.gov/products/optimum-interpolation-sst

In [1]:
import xarray as xr
import plotly.express as px

In [2]:
path_data = '/home/grupos/geocean/cagigall/geocean/DATA/HISTORICAL/SST/OISST/sst_daily_1981_2024.nc'

lon_site, lat_site = 134.368203, 7.322074

In [3]:
data_point = xr.open_dataset(path_data).sel(lon = lon_site, lat = lat_site, method = 'nearest').load()

ValueError: found the following matches with the input file in xarray's IO backends: ['netcdf4', 'h5netcdf']. But their dependencies may not be installed, see:
https://docs.xarray.dev/en/stable/user-guide/io.html 
https://docs.xarray.dev/en/stable/getting-started-guide/installing.html

In [152]:
# Convert dataset to DataFrame
df = data_point.to_dataframe()

# Add the connecting line for 'sst' points
line_trace = px.line(df, x=data_point.time.values, y='sst').data[0]
line_trace.line.update(width=0.5, color='grey')
line_trace.name = 'Daily SST'

fig = go.Figure(line_trace)

# Add the connecting line for 'sst' points first, so it appears behind other traces
df_monthly_mean = df.resample('M').mean()
line_trace_monthly = px.line(df_monthly_mean, x=df_monthly_mean.index.values, y='sst').data[0]
line_trace_monthly.line.update(width=2, color='royalblue')
line_trace_monthly.name = 'Monthly Mean SST'

fig.add_trace(line_trace_monthly)


# Create the scatter plot with OLS trendline and customize styles
scatter_fig = px.scatter(df, x=data_point.time.values, y='sst', trendline="ols")
scatter_fig.data[0].name = 'Trend line'
scatter_fig.data[0].marker.update(color='plum', size=3)  # scatter points
scatter_fig.data[1].line.update(color='darkmagenta', width=3)  # OLS trendline

# Add scatter plot traces to the main figure
fig.add_traces(scatter_fig.data)
fig.add_trace(scatter_fig.data[1])

# Set x-axis range and show the final figure
fig.update_layout(xaxis_range=[data.time.values[0], data.time.values[-1]])
fig.update_layout(title='SST OISST')
fig.update_layout(
    title='SST OISST',
    xaxis_title='Time',
    yaxis_title='SST [C]',
    legend_title='Legend'
)
fig.show()


In [109]:
data = xr.open_dataset(path_data).sel(lon = slice(lon_site-1, lon_site+1), lat = slice(lat_site-1, lat_site+1)).load()

In [155]:
df = data.mean(dim = 'time').to_dataframe().reset_index()

fig = go.Figure(go.Heatmap(
    z=df['sst'],  # replace 'value' with the column containing the heatmap values
    x=df['lon'],    # replace 'lon' with the column containing the longitude values
    y=df['lat'],    # replace 'lat' with the column containing the latitude values
    colorscale='Reds'  # specify the colorscale for the heatmap
))

fig.update_layout(
    title='Interactive Heatmap',
    xaxis_title='Longitude',
    yaxis_title='Latitude',
    autosize=False,
    width=800,
    height=600
)

fig.update_geos(
    showcoastlines=True,  # show coastlines
    coastlinecolor='black',  # set coastline color
    coastlinewidth=1  # set coastline line width
)

fig.show()
